<a href="https://colab.research.google.com/github/galrat/parsing/blob/main/Personal_parser_google_espacenet.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# установка пакетов

In [ ]:
# установка пакетов
!pip install selenium
!pip install langid
from bs4 import BeautifulSoup
from google.colab import files

from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as ec
from selenium.webdriver.support.ui import WebDriverWait

import pandas as pd
import requests
import time

import re
import langid

# Что нужно сделать для получения таблицы с патентами:
1. ниже надо ввести номера патентов для парсинга
2. затем нажать ctrl+F9 или выбрать Runtime->Run all в меню сверху

In [ ]:
# original numbers for parsing
numbers = '''US-2006276566-A1
CN-101603951-B
CN-108368203-B
CN-112778460-B
CN-111454388-B
CN-103626891-A
CN-108105590-B
CN-106523919-A
CN-103030740-B
CN-101544766-B
CN-102453260-A
MX-2007015624-A
CN-103626892-A
CN-1536010-A
CN-114316308-A
CN-1536009-A
CN-111120871-A
CN-114515554-A
US-2004116630-A1
CN-108662437-A
CN-106402660-A
CN-1566168-A
CN-106545750-B
CN-116854853-A
CN-109232779-B
'''

# основной код

## defs

In [ ]:
def separate_languages(text):
    sentences = text.split('.')  # You can use a more sophisticated sentence tokenizer based on your text

    english_text = []
    other_languages_text = []

    for sentence in sentences:
        # Use langid to identify the language of each sentence
        lang, confidence = langid.classify(sentence)

        if lang == 'en':
            english_text.append(sentence)
        else:
            other_languages_text.append(sentence)

    return ' '.join(english_text)

In [ ]:
def get_claim_google(soup):
  all = soup.find_all('div', class_='flex flex-width style-scope patent-result')[-1].find_all('div', class_='claim-text style-scope patent-text')[1]
  return all.text

def get_claim_google_2(soup):
  try:
      # all
      try:
          try:
              all = soup.find('div', class_='claim-text style-scope patent-text').find('span', class_='notranslate style-scope patent-text').text
          except:
              all = soup.find('div', class_='claim-text style-scope patent-text').text
          #print('all', all)
      except:
          all = soup.find('section', id='claims').find('span', class_='notranslate style-scope patent-text').text
          #print('all', all)

      # original
      try:
          original = soup.find('div', class_='claim-text style-scope patent-text').find('span',
                                                                                        class_='notranslate style-scope patent-text').find(
              'span').text
      except:
          try:
              original = soup.find('section', id='claims').find('span',
                                                                class_='notranslate style-scope patent-text').find(
                  'span').text
          except:
              original = ''
      #print('original', original)

      # translation
      claim_1 = all.replace(original, '')
      #print('claim 1:', claim_1)
  except:
      claim_1 = 'no_data'
  if claim_1 == '' or claim_1 == 'no_data':
    try:
      claim_1 = soup.find_all('div', class_='flex flex-width style-scope patent-result')[-1].find_all('div', class_='claim-text style-scope patent-text')[1].text
    except:
      claim_1 = 'no_data'
  return claim_1

In [ ]:
def get_data_from_google_patent(url):
  options = Options()
  options.add_argument("--headless")
  options.add_argument('--no-sandbox')
  options.add_argument('--user-agent=Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/92.0.4515.131 Safari/537.36')
  driver = webdriver.Chrome(options=options)
  driver.get(url)
  WebDriverWait(driver, 20).until(ec.visibility_of_element_located((By.ID, 'content')))
  soup = BeautifulSoup(driver.page_source, 'lxml')

  # find US, EP, WO patent document

  others = soup.find('div', class_='event style-scope application-timeline')
  text = others.find_all(class_='style-scope application-timeline')[0]
  other_apps = ''
  for t in others.find_all(class_='style-scope application-timeline'):
      try:
        other_apps += t.get('data-result').split('patent/')[1].split('/')[0] + ','
      except:
        other_apps = other_apps
  print('other_apps', other_apps)

  new_app = ''
  for app_number in other_apps.split(','):
    #print('app_number', app_number)
    if 'US' in app_number:
      new_app = app_number
      break
    if 'EP' in app_number:
      new_app = app_number
      #break
    if 'WO' in app_number:
      new_app = app_number
      #break
  if new_app != '':
    url = 'https://patents.google.com/patent/' + new_app + '/en'
    print('new_url', url)
    options = Options()
    options.add_argument("--headless")
    options.add_argument('--no-sandbox')
    options.add_argument('--user-agent=Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/92.0.4515.131 Safari/537.36')
    driver = webdriver.Chrome(options=options)
    driver.get(url)
    WebDriverWait(driver, 20).until(ec.visibility_of_element_located((By.ID, 'content')))
    soup = BeautifulSoup(driver.page_source, 'lxml')
  else:
    print('url is not changed', url)

  # title
  title = soup.find('div', id='wrapper').find('h1', id='title').text.replace('\n', '').strip()
  #print('title:', title)

  # patent_number
  patent_number = soup.find('h2', id='pubnum').text.strip().replace('\n', '').replace('\t', '')
  #print('patent_number:', patent_number)

  # applicant
  author_counter = 0
  applicant_counter = 0
  counter = 0
  author_check = 0
  applicant_check = 0
  important_people_data = soup.find('dl', class_='important-people style-scope patent-result')
  for i in important_people_data.find_all('dt', class_='style-scope patent-result'):
      if 'Inventor' in i.text:
          author_counter = counter
          author_check = 1
      if 'Assignee' in i.text:
          applicant_counter = counter
          applicant_check = 1
      counter += 1
  #print('author_counter', author_counter, 'applicant_counter', applicant_counter)

  authors = ''
  if author_check == 1:
      try:
          authors_data = soup.find('dl', class_='important-people style-scope patent-result')
          authors_data = authors_data.find_all('dt', class_='style-scope patent-result')[
              author_counter].find_next_siblings('dd')
          for author in authors_data:
              if '\n' in author.text:
                  break
              authors = authors + author.text + ';'
          authors = authors.replace('\n', '')
      except:
          #print('no authors data')
          authors = ('no authors data')
  else:
      authors = 'no_data'

  applicants = ''
  if applicant_check == 1:
      try:
          applicants_data = soup.find('dl', class_='important-people style-scope patent-result')
          applicants_data = applicants_data.find_all('dt', class_='style-scope patent-result')[
              applicant_counter].find_next_siblings('dd')
          for applicant in applicants_data:
              applicants = applicants + applicant.text.strip() + ';'
          applicants = applicants.replace('\n', '').strip()
      except:
          #print('no applicants data')
          applicants = ('no applicants data')
  else:
      applicants = 'no_data'

  # filing_date
  filind_date = 'no_data'
  publication_date = 'no_data'
  status = 'no_data'
  dates_data = soup.find_all('div', class_='event layout horizontal style-scope application-timeline')
  for data in dates_data:
      if 'filed by' in data.text:
          filind_date = data.text.split('Application')[0]
          #print('filing date:', filind_date)
      if 'Publication' in data.text:
          publication_date = data.text.split('Publication')[0]
          #print('Publication date:', publication_date)
      if 'Status' in  data.text:
          status = data.text.split('Status')[1].replace('\n', '').replace('\t', '')
          #print('Status:', status)

  # application number
  try:
      application_number = soup.find_all('div', class_='header style-scope application-timeline')[1].text
      application_number = application_number.split('Application')[1].split('events')[0].replace(' ','')
  except:
      print('no application number data')
      application_number = 'no data'
  #print('application_number', application_number)

  # get priority applications
  priority_applications = ''
  for i in soup.find('div', class_='wrap style-scope application-timeline').find_all('div', class_='event layout horizontal style-scope application-timeline'):
    try:
      priority_applications += i.text.split('Priority to')[1].strip() + ';'
      #print(i.text.split('Priority to')[1].strip())
    except:
      no_priority = 1
  if priority_applications == '':
    priority_applications = 'no_data'

  # ipc
  ipc_data = 'no_data'
  try:
      ipcs = soup.find('div', class_='style-scope classification-viewer').find_all('div', class_='style-scope classification-tree')
      for ipc in ipcs:
          ipc_class = ipc.find(first=True).text.strip().replace('\n', '').replace('\t', '')
          #print('ipc', ipc_class)
      #print(ipc_class)
  except:
      ipc_data = 'no_data'

  ipc_datas = soup.find_all('div', class_='style-scope classification-tree')
  for i in ipc_datas[:1]:
      target = i.find_all(class_='code style-scope classification-tree')
      #print('target ipc', target[-1].text)
      # print(i.text.strip())
      ipc_data = target[-1].text

  # claim 1
  claim_1 = ''
  try:
    claim_1 = get_claim_google_2(soup)
    #print('claim_1 google', claim_1)
  except:
    print('no claims')
  claim_1 = claim_1.split('according to claim')[0].replace('\n', '').replace('\t', ' ')

  # abstract
  abstract = ''
  try:
    abstract_orig = soup.find('section', id='abstract').find('span', class_='google-src-text style-scope patent-text').text#.text.replace('\n', '').replace('\t', '').replace('Abstracttranslated from ', '')
    #print('abstract_orig', abstract_orig)
    abstract_all = soup.find('section', id='abstract').text
    #print('abstract_all', abstract_all)
    abstract_eng = abstract_all.replace(abstract_orig, '').strip()
    abstract_eng = abstract_eng.replace('\n', '')
    #print('abstract_eng', abstract_eng)
    abstract = abstract_eng
  except:
    abstract = soup.find('section', id='abstract').text.replace('\n', '').replace('\t', ' ')

  # set 'printing = 1' to show info
  printing = 0
  while printing:
      print('patent_number:', patent_number)
      print('application_number:', application_number)
      print('title:', title)
      print('priority_applications:', priority_applications)
      print('filind_date:', filind_date)
      print('applicant:', applicants)
      print('authors:', authors)
      print('ipc_data:', ipc_data)
      print('publication_date:', publication_date)
      print('abstract:', abstract)
      print('claim_1:', claim_1)
      print('status:', status)
      print('others:', other_apps)
      break

  header = ['patent number', 'application_number', 'title', 'INV/UM', 'filing_date', 'applicant', 'autors',
                          'publiction_date', 'ipc', 'claims', 'status', 'abstract', 'other_applications']
  data_line = []
  data_line.append(patent_number)
  data_line.append(application_number)
  data_line.append(title)
  data_line.append(priority_applications)
  data_line.append(filind_date)
  data_line.append(applicants)
  data_line.append(authors)
  data_line.append(publication_date)
  data_line.append(ipc_data)
  data_line.append(claim_1.replace('\n', ''))
  data_line.append(status)
  data_line.append(abstract.replace('\n', ''))
  #data_line.append(others[:-1])
  data_line.append(other_apps)

  # data from the bottom reagrding similar patents

  add_patents = soup.find('div', class_='footer style-scope patent-result').find_all('div', class_='responsive-table style-scope patent-result')[0].find_all('div', class_='tr style-scope patent-result')
  patent_lines = []
  for patent in add_patents:
    patent_line = []
    for line in patent.find_all('span'):
      #print(line.text.replace('*', '').strip())
      patent_line.append(line.text.replace('*', '').strip())
      #print('---------------------')
    #print(patent.find('span'))
    patent_lines.append(patent_line)
    #print('===========================')
    #break

  add_patents = soup.find('div', class_='footer style-scope patent-result').find_all('div', class_='responsive-table style-scope patent-result')[1].find_all('div', class_='tr style-scope patent-result')
  for patent in add_patents:
    patent_line = []
    for line in patent.find_all('span'):
      #print(line.text.replace('*', '').strip())
      patent_line.append(line.text.replace('*', '').strip())
      #print('---------------------')
    #print(patent.find('span'))
    if len(patent_line) == 3:
      patent_line.insert(1, 'no_data')
      patent_line.insert(3, 'no_data')
    patent_lines.append(patent_line)
    #print('===========================')
    #break

  add_patents = soup.find('div', class_='footer style-scope patent-result').find_all('div', class_='responsive-table style-scope patent-result')[2].find_all('div', class_='tr style-scope patent-result')
  for patent in add_patents:
    patent_line = []
    for line in patent.find_all('span'):
      #print(line.text.replace('*', '').strip())
      patent_line.append(line.text.replace('*', '').strip())

      #print('---------------------')
    #print(patent.find('span'))
    if len(patent_line) == 3:
      patent_line.insert(1, 'no_data')
      patent_line.insert(3, 'no_data')
    patent_lines.append(patent_line)
    #print('===========================')
    #break

  # get data for espacenet
  all_additional_urls = [url.get('href') for url in soup.find('dl', class_='links style-scope patent-result').findAll('a')]

  return data_line, patent_lines, all_additional_urls


In [ ]:
def get_from_espacenet(espacenet_url):
    #print('def', espacenet_url)
    data_line2 = []

    options = Options()
    options.add_argument("--headless")
    options.add_argument('--no-sandbox')
    options.add_argument('--user-agent=Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/92.0.4515.131 Safari/537.36')
    driver = webdriver.Chrome(options=options)
    driver.get(espacenet_url)
    time.sleep(2)
    WebDriverWait(driver, 20).until(ec.visibility_of_element_located((By.ID, 'pagebody')))

    soup = BeautifulSoup(driver.page_source, 'lxml')

    #print(soup.text)
    #print('---------------------\n')
    # title
    title = soup.find('h3').text.strip().replace('\n', '').replace('\t', '')
    #print('title:', title)
    table = soup.find('table', class_='tableType3')
    #print(table.text.strip())
    app_num = soup.find('h1', class_='noBottomMargin').text.split('―')[0].split('\n')[-1].strip().replace('\xa0', '').replace('(', '').replace(')', '')

    applicant = ''
    authors = ''
    ipc = ''
    priority = ''
    original_application = ''
    others= ''

    table_lines = table.find_all('tr')
    for line in table_lines:
      if 'Applicant(s):' in line.text:
        applicant = ' '.join(line.find('td').text.replace('\n', '').replace('\t', '').strip().split())
        applicant = applicant.split('+')[0].strip()
        #print('applicant:', applicant)

      if 'Inventor(s):' in line.text:
        authors = ' '.join(line.find('td').text.replace('\n', '').replace('\t', '').strip().split())
        authors = authors.split('+')[0].strip()
        #print('authors:', authors)

      if 'Classification:' in line.text:
        ipc = ' '.join(line.find('td').text.replace('\n', '').replace('\t', '').strip().split()).split('- cooperative')[0]
        ipc = ipc.replace('- international:', '').strip()
        ipc = ipc.split('(IPC1-7)')[0].strip()
        #print('ipc:', ipc)

      if 'Priority number(s):' in line.text:
        priority = ' '.join(line.find('td').text.replace('\n', '').replace('\t', '').strip().split()).split('- cooperative')[0]
        #print('Priority:', priority)

      if 'Application number:' in line.text:
        original_application = ' '.join(line.find('td').text.replace('\n', '').replace('\t', '').strip().split()).split('- cooperative')[0]
        original_application = original_application.replace('Global Dossier', '').strip()
        #print('original_application:', original_application)

      if 'Also published as:' in line.text:
        others = ' '.join(line.find('div', id='lessPublishedAs').text.replace('\n', '').replace('\t', '').strip().split()).split('- cooperative')[0]
        #others = soup.find('div', id='lessPublishedAs').text.strip()
        #print('others:', others)


    publication = 'no_data'

    abstract = soup.find('div', class_='application article clearfix').find('p').text.replace('\t', ' ').replace('\n', '')
    #print(abstract)

    printing = 0
    while printing:
        print('title:', title)
        print('applicant:', applicant)
        print('authors:', authors)
        print('ipc:', ipc)
        print('priority:', priority)
        print('original_application:', original_application)
        print('publication:', publication)
        print('abstract:', abstract)
        print('others:', others)
        break

    data_line2.append(app_num)
    data_line2.append(applicant)
    data_line2.append(authors)
    data_line2.append(ipc)
    data_line2.append(priority)
    data_line2.append(original_application)
    data_line2.append(publication)
    data_line2.append(title)
    data_line2.append(abstract)
    data_line2.append(others)

    header = ['patent_number2', 'applicant2', 'authors2', 'ipc2', 'priority2', 'original2', 'publication2', 'title', 'abstract', 'other_applications']

    return (data_line2)

## code

In [ ]:
numbers = numbers.replace('-', '')
all_numbers = numbers.split()
print('lenght of all_numbers', len(all_numbers))

lenght of all_numbers 1925


In [ ]:
file_for_saving_results = "/content/saved_data.txt"

header_1 = ['patent number', 'applicant2', 'authors2', 'ipc2', 'priority2', 'original2', 'publication2', 'title_2', 'abstract_2',
              'other_applications_2']
header_2 = ['patent number', 'application_number', 'title', 'priority applications', 'filing_date', 'applicant', 'authors',
                            'publiction_date', 'ipc', 'claims', 'status', 'abstract', 'other_applications']
try:
    saved_data = pd.read_csv(file_for_saving_results, sep='\t')
    parsed_numbers = saved_data['original_number'].values
except:
    parsed_numbers = []
    with open(file_for_saving_results, 'a', encoding="utf-8") as file:
        file.writelines('\t'.join(['original_number'] + header_2 + header_1) + '\n')
    print("creating new file")

remaining_numbers = list(set(all_numbers) - set(parsed_numbers))
print('remaining_numbers', remaining_numbers)
print('total remaining', len(remaining_numbers))

creating new file
remaining_numbers ['KR20200127818A', 'CN112861743A', 'CN117058723B', 'US8121356B2', 'CN104239769A', 'EP1780657A2', 'CN114241535A', 'WO2014031983A2', 'FR3112008B1', 'US11531743B2', 'AU2020432845B2', 'CN111639559B', 'CN104217207A', 'US20130202182A1', 'US20150186708A1', 'CN110852160B', 'CN108960125A', 'US20100208949A1', 'CN109377473A', 'US8606097B2', 'US20140230033A1', 'CN109190460B', 'CN110414330A', 'al.', 'US20150113634A1', 'US10484584B2', 'US11423687B2', 'CN102184404A', 'JP2006218019A', 'CN111861999A', 'CN108319911A', 'CN106295622A', 'CH716053A1', 'US10552658B2', 'CN109977909A', 'US20230316790A1', 'JP7269711B2', 'CN113963158A', 'US20080253622A1', 'CN113593092A', 'WO2023210081A1', 'CN106548176B', 'CN116798077A', 'CN108197577B', 'JP2009031903A', 'US8520903B2', 'US10395128B2', 'CN110298944B', 'US20150242840A1', 'US20060244947A1', 'US11449598B2', 'US20150278499A1', 'CN110598640B', 'JP4762572B2', 'JP2014142881A', 'US20120281884A1', 'JP2008004001A', 'US20150254492A1', 'US89

In [ ]:
# correct app_numbers
remaining_numbers_corrected = []
for number in remaining_numbers:
    if number[:2] == 'WO' and len(number) == 12:
        number = 'WO20' + number[2:] + '/en'
    remaining_numbers_corrected.append(number)

final_urls = []
for app_num in remaining_numbers_corrected:
  if app_num[:3] == 'US2' and len(app_num) == 14:
      url =  app_num[:].replace('-', '')[:6] + '0' + app_num[:].replace('-', '')[6:] + '/en'
      url = 'https://patents.google.com/patent/' + url
      #print('corrected url', url)
  else:
      url = 'https://patents.google.com/patent/' + app_num[:].replace('-', '').replace('\n', '') + '/en'
      #print('url', url)
  final_urls.append(url)

print(final_urls)


['https://patents.google.com/patent/KR20200127818A/en', 'https://patents.google.com/patent/CN112861743A/en', 'https://patents.google.com/patent/CN117058723B/en', 'https://patents.google.com/patent/US8121356B2/en', 'https://patents.google.com/patent/CN104239769A/en', 'https://patents.google.com/patent/EP1780657A2/en', 'https://patents.google.com/patent/CN114241535A/en', 'https://patents.google.com/patent/WO2014031983A2/en', 'https://patents.google.com/patent/FR3112008B1/en', 'https://patents.google.com/patent/US11531743B2/en', 'https://patents.google.com/patent/AU2020432845B2/en', 'https://patents.google.com/patent/CN111639559B/en', 'https://patents.google.com/patent/CN104217207A/en', 'https://patents.google.com/patent/US20130202182A1/en', 'https://patents.google.com/patent/US20150186708A1/en', 'https://patents.google.com/patent/CN110852160B/en', 'https://patents.google.com/patent/CN108960125A/en', 'https://patents.google.com/patent/US20100208949A1/en', 'https://patents.google.com/paten

# результаты


In [ ]:
# get data by url
counter = 1
wrong_numbers = []
bottom_data = []
espacenet_urls = []
for original_number, url in zip(remaining_numbers, final_urls[:]):
  print(counter, '/', len(remaining_numbers))
  counter += 1
  print(url)
  try:
    data_line_google = get_data_from_google_patent(url)
    print('data_line_google', data_line_google[0])
    print(data_line_google[1])
    bottom_data += data_line_google[1]

    # get espacenet url
    all_additional_urls = data_line_google[2]
    for url in all_additional_urls:
      if 'espacenet' in url:
        #print('espacenet_url from google', url)
        espacenet_url = url
        espacenet_urls.append(espacenet_url)
        break

    # get data using espacent url
    try:
      o/0
      print('espacenet_url', espacenet_url)
      data_line_espacenet = get_from_espacenet(espacenet_url)
      print('data_line_espacenet', data_line_espacenet)
      print()
    except:
      data_line_espacenet = header_1
      print('smth wrong with espacenet')

    with open(file_for_saving_results, 'a', encoding="utf-8") as file:
        file.writelines('\t'.join([original_number] + data_line_google[0] + data_line_espacenet) + '\n')
        #print('writing')
  except:
    wrong_numbers.append(original_number)



  print()
  #break
print('====================finish=========================')
print('wrong_numbers which shall be reparsed', wrong_numbers)

# download the created file
files.download(file_for_saving_results)

Streaming output truncated to the last 5000 lines.
other_apps JP4340618B2,US7526110B2,EP1645990B1,KR100677690B1,
new_url https://patents.google.com/patent/US7526110B2/en
data_line_google ['US7526110B2', 'US11/084,168', 'Biometric information authentication device, biometric information authentication method, and computer-readable recording medium with biometric information authentication program recorded thereon', 'no_data', '2005-03-21', 'Fujitsu Ltd;', 'Koichiro Niinuma;Satoshi Semba;Takashi Shinzaki;', '2009-04-28', 'G06V40/1365', '1. A biometric information authentication device comprising:an obtaining section for obtaining biometric information of an authentication object;a first extraction section for extracting first to-be-verified data to be used in a minutia matching method from said biometric information obtained by said obtaining section;a second extraction section for extracting second to-be-verified data to be used in a pattern matching method from said biometric informati

In [ ]:
bottom_data_2 = []

for line in bottom_data[1:]:
  if len(line) == 5 and 'Family To Family Citations' not in line[0] and 'Priority date' not in line[1]:
    bottom_data_2.append(line)

bottom_data_df = pd.DataFrame(bottom_data_2[0:], columns=['Publication number', 'Priority date', 'Publication date',  'Assignee',  'Title'])
bottom_data_df.to_csv('bottom_data.csv')
files.download('bottom_data.csv')
bottom_data_df

In [ ]:
!pip install wordcloud matplotlib

from wordcloud import WordCloud, STOPWORDS
import matplotlib.pyplot as plt

In [ ]:
# Example list of words
word_list = bottom_data_df['Title'].values

stop_words = ['system', 'method', 'device', 'apparatus', 'systems', 'methods']

text = ' '.join(word_list)

# Define custom stop words
custom_stopwords = set(stop_words)

# Add custom stop words to the default set of stop words
stopwords = set(STOPWORDS).union(custom_stopwords)

# Generate the word cloud with custom stop words
wordcloud = WordCloud(width=800, height=400, background_color='white', stopwords=stopwords).generate(text)

# Display the word cloud using matplotlib
plt.figure(figsize=(15, 10))
plt.axis('off')
plt.imshow(wordcloud)#, interpolation='bilinear')

In [ ]:
# фильтрация патентов из нижней части по слову в названии
filter = 0
if filter:
  bottom_data_df.dropna(inplace=True)
  bottom_data_df = bottom_data_df[bottom_data_df.Title.str.contains('heavy') | bottom_data_df.Title.str.contains('asphalt')]

  bottom_data_df.to_csv('bottom_data.csv')
  #files.download('bottom_data_filtered.csv')

# tests part
